<a href="https://colab.research.google.com/github/MayaCutkosky/QuantumNoiseModel/blob/main/ErrorModel.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Data structure
## Important operations on density matrices

### Partial trace

Let $\rho = A \otimes B \otimes C$
$A \in \mathbb{C}^{m\times m}$
$C \in \mathbb{C}^{n\times n}$


$$\rho = \begin{bmatrix}
a_{00}b_{00} C & a_{00}b_{10} C & a_{10} b_{00} C & a_{10} b_{10} C & \ldots & a_{n0}b_{00} C & a_{n0}b_{10} C \\
\ldots\\
a_{0n}b{01} C & a_{0n}b_{11}C & a_{1n} b_{01} C & a_{1n} b_{11} C & \ldots &  a_{nn}b_{01}C & a_{nn}b_{11} C \\
\end{bmatrix}$$



$$Tr_B (\rho) = \begin{bmatrix}
a_{00} C & \ldots & a_{n0} C \\
\ldots \\
a_{0n} C & \ldots a_{nn} C \\
\end{bmatrix} =
\begin{bmatrix}
\rho_{0,0} + \rho_{m,m} & \rho_{1,0} + \rho_{m+1,m} & \rho_{2m,0} + \rho_{3m,m} & \ldots &  \rho_{2m+1,0} + \rho_{3m+1,1} & \ldots & \rho_{nm-m, 0} + \rho_{nm - m + 1,m} \\
\ldots \\
\rho_{0,(n-1)m } + \rho_{m,nm-1} & \ldots  \\
\end{bmatrix}$$



# Gates and qubit counting

Gates are ordered by type and qubits.
For instance gate_operator[type][qubits] would get a gate operator for the specific type and qubits

In [ ]:
import numpy as np
def operator(x):
    n = len(x)
    M = Operator((n,n),complex, buffer= np.array(x, dtype = complex))
    return M
def kraus(x):
    x = np.array(x, dtype = complex)
    M = Kraus(x.shape,complex, buffer= x)
    return M

class Operator(np.ndarray):
    def __new__(cls, *args, **kwargs):
        instance = super().__new__(cls, *args, **kwargs)
        return instance
    def __mul__(self,y):
        if isinstance(y, Operator):
            return np.matmul(self,y)
        else:
            return super().__mul__(y)
    def tensor(self, y):
        return np.kron(self,y)

    def adjoint(self):
        return np.swapaxes(np.conj(self),-1,-2)

    def is_unitary(self):
        return self * self.adjoint() == np.identity(len(self))

    def __eq__(self,x):
      return np.max(self - x) < 1e-10


class Kraus(Operator):
    pass

class DensityMatrix(Operator): #allow for list of DensityMatrices
    def transition(self,U : Operator):
        is_Kraus = isinstance(U,Kraus)
        if is_Kraus and len(U.shape) > 3:
            U = np.swapaxes(U,0,-3)
        output = U * self * U.adjoint()
        if isinstance(U, Kraus):
            if len(U.shape) > 3:
                output = density_matrix(np.swapaxes(output,0,-3))
            output = output.sum(axis = -3)
        return density_matrix(output)

    def partial_trace(self, i):
        #shape : s, i,j
        n = int(2 ** i)
        m = len(self) // (2*n)

        ind = np.tile(np.arange(m),n) + np.arange(n).repeat(m)*2*m
        i1 = np.tile(ind,[len(ind),1])
        j1 = i1.T
        i2 = i1 + m
        j2 = i2.T

        return self[...,i1,j1] + self[...,i2,j2]

    def measure(self, psi):
        output = np.matmul(np.matmul([psi], rho),psi)
        assert output.imag == 0
        return output.real[0]


def density_matrix(x):
    if len(np.shape(x)) == 1: # x is a state
        #make x a proper state
        x = x / np.linalg.norm(x)
        x = np.matmul(np.expand_dims(x,1),[x])
    rho = DensityMatrix(np.shape(x), complex, np.array(x, dtype = complex))
    assert rho.shape[-1] == rho.shape[-2]
    return rho

In [ ]:
import jax.numpy as jnp
import numpy as np

def operator(x):
    n = len(x)
    M = Operator((n,n),complex, buffer= np.array(x, dtype = complex))
    return M
def kraus(x):
    x = np.array(x, dtype = complex)
    M = Kraus(x.shape,complex, buffer= x)
    return M

class Operator:
    def __init__(self, shape = [2,2], dtype = complex, buffer = None, data_object = None):

        if data_object is None:
            if buffer is None:
                self.data_object = "numpy"
            else:
                self.data_object = self.find_data_type(buffer)

        if data_object == 'jax':
            if buffer is None:
                self.data = jnp.zeros(shape)
            else:
                self.data = jnp.array(buffer)
        elif data_object == 'numpy':
            shape = buffer.shape
            self.data = np.ndarray(shape, dtype, buffer)
    @staticmethod
    def find_data_type(data):
        data_object = str(type(data))
        if "numpy" in data_object:
            data_object = "numpy"
        elif "jax" in data_object:
            data_object = "jax"
        return data_object

    def __mul__(self,y):
        if isinstance(y, Operator):
            data = np.matmul(self.data,y.data)
        else:
            data = self.data * y
        return self.__init__(buffer = data)

    def __add__(self, y):
        if isinstance(y, Operator):
            data = self.data + y.data
        else:
            data = self.data + y
        return self.__init__(buffer = data)

    def tensor(self, y):
        data = np.kron(self.data,y)
        return self.__init__(buffer = data)

    def adjoint(self):
        data = np.swapaxes(np.conj(self.data),-1,-2)
        return self.__init__(buffer = data)

    def is_unitary(self):
        return self * self.adjoint() == np.identity(len(self))

    def __eq__(self,x):
      return np.max(np.abs(self.data - x.data)) < 1e-10


class Kraus(Operator):
    pass

class DensityMatrix(Operator): #allow for list of DensityMatrices
    def transition(self,U : Operator):
        is_Kraus = isinstance(U,Kraus)
        if is_Kraus and len(U.shape) > 3:
            U = np.swapaxes(U,0,-3)
        output = U * self * U.adjoint()
        if isinstance(U, Kraus):
            if len(U.shape) > 3:
                output = density_matrix(np.swapaxes(output,0,-3))
            output = output.sum(axis = -3)
        return density_matrix(output)

    def partial_trace(self, i):
        #shape : s, i,j
        n = int(2 ** i)
        m = len(self) // (2*n)

        ind = np.tile(np.arange(m),n) + np.arange(n).repeat(m)*2*m
        i1 = np.tile(ind,[len(ind),1])
        j1 = i1.T
        i2 = i1 + m
        j2 = i2.T

        return self[...,i1,j1] + self[...,i2,j2]

    def measure(self, psi):
        output = np.matmul(np.matmul([psi], rho),psi)
        assert output.imag == 0
        return output.real[0]


def density_matrix(x):
    if len(np.shape(x)) == 1: # x is a state
        #make x a proper state
        x = x / np.linalg.norm(x)
        x = np.matmul(np.expand_dims(x,1),[x])
    rho = DensityMatrix(np.shape(x), complex, np.array(x, dtype = complex))
    assert rho.shape[-1] == rho.shape[-2]
    return rho

True

In [ ]:
a = jax.numpy.array([3,2])
def sum_logistic(x):
  return jax.numpy.sum(1.0 / (1.0 + jax.numpy.exp(-x)))

x_small = jax.numpy.arange(3.)
derivative_fn = jax.grad(sum_logistic)
print(derivative_fn(x_small))
np.array([])

In [ ]:
a = density_matrix(np.random.rand(2))
b = density_matrix(np.random.rand(2))
c = density_matrix(np.random.rand(2))

rho = a.tensor(b).tensor(c)
b.tensor(c) == rho.partial_trace(0)

DensityMatrix(True)

In [ ]:
U = kraus(np.random.rand(3,2,2))
U * a == [u * a for u in U]

Kraus(True)

In [ ]:
class System:
    def __init__(self,size = None, config = None):
        if config is None:
            self.rho = density_matrix(size * [[[1,0],[0,0]]])
            self.careful_mode = True
        else:
            for key, value in config.items():
                setattr(self, key, value)
    def transition_qubit(self,U, qubits, in_place = True):
        if not in_place:
            sys = System(self.config())
            sys.transition_qubit(self, U, qubits)
            return sys
        if self.careful_mode:
            assert U.is_unitary
            assert U.shape[-1] == U.shape[-2]
            assert U.shape[-1] == 2 ** len(qubits)

        if len(qubits) == 1:
            i = qubits[0]
            self.rho[i] = self.rho[i].transition(U)

        elif len(qubits) == 2:
            i,j = qubits
            combined_rho = self.rho[i].tensor(self.rho[j])
            combined_rho = combined_rho.transition(U)
            self.rho[i] = combined_rho.partial_trace(1)
            self.rho[j] = combined_rho.partial_trace(0)


    def transition(self, U, in_place = True):
        '''
            U : list of operators of length self.rho
        '''
        if not in_place:
            sys = System(self.config())
            sys.transition(U)
            return sys
        self.rho = self.rho.transition(U)



In [ ]:
sys = System(3)
U = operator([[1,1],[-1,1]]) / np.sqrt(2)
sys.transition(U)
sys.rho

DensityMatrix([[[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]],

               [[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]],

               [[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]]])

In [ ]:
sys = System(3)
sys.transition_qubit(U,[1])
sys.rho

DensityMatrix([[[ 1. +0.j,  0. +0.j],
                [ 0. +0.j,  0. +0.j]],

               [[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]],

               [[ 1. +0.j,  0. +0.j],
                [ 0. +0.j,  0. +0.j]]])

In [ ]:
sys = System(3)
sys.transition_qubit(U.tensor(U), [0,2])
sys.rho

DensityMatrix([[[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]],

               [[ 1. +0.j,  0. +0.j],
                [ 0. +0.j,  0. +0.j]],

               [[ 0.5+0.j, -0.5+0.j],
                [-0.5+0.j,  0.5+0.j]]])

In [ ]:

import itertools as it
pauli = {
    'I' : operator(np.identity(2)),
    'X' : operator([[0,1],[1,0]]),
    'Y' : operator([[0,complex(0,-1)],[complex(0,1),0]]),
    'Z' : operator([[1,0],[0,-1]])
}


def crand(**args):
    return complex(np.random.rand(**args),np.random.rand(**args))
def expi(theta):
    return np.cos(theta) + complex(0,1) * np.sin(theta)


ideal_gates = {
    'id' : operator(np.identity(2)),
    'x' : pauli['X'],
    'sx' : operator([[complex(1,1),complex(1,-1)],[complex(1,-1),complex(1,1)]])/2,
    'rz' : lambda phi : operator([[expi(-phi/2),0],[0,expi(phi/2)]]),
}
cz = np.identity(4)
cz[3,3] = -1
ideal_gates['cz'] = cz




# Load dataset and important information from qiskit.

In [ ]:
!pip install qiskit
!pip install qiskit_ibm_runtime
import qiskit
from qiskit_ibm_runtime import QiskitRuntimeService
#service = QiskitRuntimeService(token=input(), channel="ibm_quantum")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 101.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 82.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.5/49.5 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.7/49.7 MB 19.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.0/109.0 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 53.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 359.9/359.9 kB 20.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.5/69.5 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.5/130.5 kB 10.2 MB/s eta 0:00:00


In [ ]:
from qiskit.quantum_info import average_gate_fidelity, Choi
from qiskit.quantum_info import Kraus as qiskit_Kraus

In [ ]:
l = err.data
l

NameError: name 'err' is not defined

In [ ]:
import numpy as np
import warnings
def relaxation_error(prop, qubit, gate_length):
    t1,t2 = prop.t1(qubit), prop.t2(qubit)
    if t1 * 2 < t2:
        warnings.warn("t2 > 2t1 for qubit {}. Changing {} to {}".format(qubit, t2, 2 * t1))
        t2 = 2 * t1

    p_reset = 1 - np.exp(-gate_length /t1)
    exp_t2 = np.exp(-gate_length / t2)
    if p_reset - 1 < 1e-12 and exp_t2 < 1e-12:
        return np.identity(2)
    err = qiskit_Kraus(Choi(
                np.array(
                    [
                        [1, 0, 0, exp_t2],
                        [0, 0, 0, 0],
                        [0, 0, p_reset, 0],
                        [exp_t2, 0, 0, 1 - p_reset],
                    ]
                )
            ))
    err = err.data
    err.extend([np.identity(2)]*(3-len(err)))
    return err

def gate_error(gate_err, relax_err, num_qubits):
    relax_fid = average_gate_fidelity(relax_err)
    dim = 2 ** num_qubits
    depol_param = dim * (gate_err + relax_fid - 1) / (dim * relax_fid - 1)
    return depol_param / 4 ** num_qubits

def process_gate_data(g):
  gate_length = None
  gate_error = None
  for param in g.parameters:
      if param.name == 'gate_length':
        gate_length = param.value
        if param.unit == 'ns':
          gate_length *= 1e-9
      if param.name == 'gate_error':
        gate_error = param.value
  return g.gate, tuple(g.qubits), gate_error, gate_length

def get_errs_from_gate(prop, g):
    name, qubits, gate_err, gate_length = process_gate_data(g)
    relax_errs = []
    for q in range(len(prop.qubits)):
        relax_errs.append(relaxation_error(prop, q, gate_length))

    relax_gate_err = qiskit_Kraus([1])
    for q in qubits:
        relax_gate_err = relax_gate_err.expand(qiskit_Kraus(relax_errs[q]))
    depol_err = gate_error(gate_err, relax_gate_err, len(qubits))
    if depol_err < 0 :
        return kraus(relax_errs), operator(np.identity(2**len(qubits)))
    gen = it.product(pauli.keys(),repeat = len(qubits))
    gen.__next__()
    kraus_input = []
    for key_list in gen:
        pauli_err = operator([1])
        for key in key_list:
            pauli_err = pauli_err.tensor(pauli[key])
        kraus_input.append(depol_err * pauli_err)
    kraus_input.append((1-len(kraus_input)*depol_err) * np.identity(2**len(qubits)))
    return kraus(relax_errs), kraus(kraus_input)

Nduv(datetime.datetime(2025, 2, 24, 7, 48, 2, tzinfo=tzoffset(None, -18000)), prob_meas0_prep1, , 0.017578125)

In [ ]:
def get_readout_errs(q):
    probs = [None, None]
    for param in q:
        if param.name == 'prob_meas0_prep1':
            probs[0] = param.value
        elif param.name == 'prob_meas1_prep0':
            probs[1] = param.value
    return probs

In [ ]:
choi = np.array(
                    [
                        [1, 0, 0, exp_t2],
                        [0, 0, 0, 0],
                        [0, 0, p_reset, 0],
                        [exp_t2, 0, 0, 1 - p_reset],
                    ]
                )
eigenval, eigenvec = np.linalg.eig(choi)
k = []
for i in range(4):
  k.append(np.sqrt(eigenval[i]) * eigenvec[i].T.reshape((2,2)))
choi

NameError: name 'exp_t2' is not defined

In [ ]:
choi = operator(choi)
choi == choi.adjoint()

Operator(True)

In [ ]:

from toqito.channel_ops import choi_to_kraus
np.array(choi_to_kraus(choi)).round(5)

array([[[[-0.00314+0.j,  0.     +0.j],
         [ 0.     +0.j,  0.00314+0.j]],

        [[ 0.00314-0.j, -0.     +0.j],
         [-0.     +0.j, -0.00314+0.j]]],


       [[[ 0.     +0.j,  0.02973+0.j],
         [ 0.     +0.j,  0.     +0.j]],

        [[ 0.     +0.j,  0.02973+0.j],
         [ 0.     +0.j,  0.     +0.j]]],


       [[[-1.     +0.j,  0.     +0.j],
         [ 0.     +0.j, -0.99956+0.j]],

        [[-1.     +0.j,  0.     +0.j],
         [ 0.     +0.j, -0.99956+0.j]]]])

In [ ]:
from qiskit_ibm_runtime.fake_provider import FakeFez
backend = FakeFez()
prop = backend.properties()


In [ ]:
def process_backend(prop):
    errs = dict()
    for name in ['id','cz','x','sx','rz']:
        errs[name] = dict()
    connections = []
    for g in prop.gates:
        name, qubits, gate_err, gate_length = process_gate_data(g)
        if name == 'cz':
            connections.append(qubits)
        if name in ['id','cz', 'x','sx', 'rz']:
            relax_errs, depol_err = get_errs_from_gate(prop,g)
            errs[name][qubits] = {
                'relax' : relax_errs,
                'depol' : depol_err
            }
    readout_errs = np.empty([len(prop.qubits), 2])
    for i,q in enumerate(prop.qubits):
        readout_errs[i] = get_readout_errs(q)
    return len(prop.qubits), len(prop.gates), connections, errs, readout_errs
process_backend(prop)

<ipython-input-30-9c5eeba70b64>:6: UserWarning: t2 > 2t1 for qubit 87. Changing 5.6838717300148796e-05 to 5.42970235219996e-05
  warnings.warn("t2 > 2t1 for qubit {}. Changing {} to {}".format(qubit, t2, 2 * t1))


(156,
 1640,
 [(72, 73),
  (73, 72),
  (7, 17),
  (17, 7),
  (67, 68),
  (68, 67),
  (44, 45),
  (45, 44),
  (8, 9),
  (9, 8),
  (40, 41),
  (41, 40),
  (100, 101),
  (101, 100),
  (91, 98),
  (98, 91),
  (132, 133),
  (133, 132),
  (41, 42),
  (42, 41),
  (55, 59),
  (59, 55),
  (73, 74),
  (74, 73),
  (133, 134),
  (134, 133),
  (59, 75),
  (75, 59),
  (14, 15),
  (15, 14),
  (9, 10),
  (10, 9),
  (74, 75),
  (75, 74),
  (39, 53),
  (53, 39),
  (129, 130),
  (130, 129),
  (106, 107),
  (107, 106),
  (83, 96),
  (96, 83),
  (111, 112),
  (112, 111),
  (138, 151),
  (151, 138),
  (47, 48),
  (48, 47),
  (42, 43),
  (43, 42),
  (47, 57),
  (57, 47),
  (107, 108),
  (108, 107),
  (134, 135),
  (135, 134),
  (144, 145),
  (145, 144),
  (48, 49),
  (49, 48),
  (77, 85),
  (85, 77),
  (103, 104),
  (104, 103),
  (80, 81),
  (81, 80),
  (85, 86),
  (86, 85),
  (131, 138),
  (138, 131),
  (140, 141),
  (141, 140),
  (36, 41),
  (41, 36),
  (71, 72),
  (72, 71),
  (81, 82),
  (82, 81),
  (108,

In [ ]:

errs = dict()
for name in ['id','cz','x','sx','rz']:
  errs[name] = dict()
connections = []
for g in prop.gates:
        name, qubits, gate_err, gate_length = process_gate_data(g)
        if name == 'cz':
            connections.append(qubits)
        if name in ['id','cz', 'x','sx', 'rz']:
            relax_errs, depol_err = get_errs_from_gate(prop,g)
            errs[name][qubits] = {
                'relax' : relax_errs,
                'depol' : depol_err
            }


<ipython-input-83-05c60a9fbfbd>:6: UserWarning: t2 > 2t1 for qubit 87. Changing 5.6838717300148796e-05 to 5.42970235219996e-05
  warnings.warn("t2 > 2t1 for qubit {}. Changing {} to {}".format(qubit, t2, 2 * t1))


In [ ]:
average_gate_fidelity(qiskit_Kraus(relaxation_error(prop,qubits[0], gate_length)))

0.9997293467213186

In [ ]:
a = np.array([4,2])
a.expand

AttributeError: 'numpy.ndarray' object has no attribute 'expand'

In [ ]:
qc = qiskit.QuantumCircuit(3)
qc.rz(np.pi/2,1)
qiskit.transpile(qc, backend = backend).draw(idle_wires = False)

┌─────────┐
q_1 -> 4 ┤ Rz(π/2) ├
         └─────────┘

### Load Data

In [ ]:
import zipfile
f = zipfile.ZipFile('QuantumCrosstalkData.zip')
import json
d = json.loads( f.read('data_aggregationMarch6.json') )

In [ ]:
def load_circuit(filename):
  with f.open('TranspiledCircuits/' + filename, 'r') as fd:
      circuits = qiskit.qpy.load(fd)
  return circuits

def translate_circuit(circuit):
    return [ [inst.name, [q._index for q in inst.qubits], inst.params] for inst in circuit.data]

In [ ]:
circuit = load_circuit(d[0]['filename'])[0]
circ = []
measurement_gate_inds = []
for i, inst in enumerate(circuit):
    if inst.name == 'measure':
        measurement_gate_inds.append(i)
    if inst.name in ['barrier','measure']:
        continue
    qubits = tuple([q._index for q in inst.qubits])
    circ.append([inst.name, qubits, inst.params])
readout_qubits = np.empty(len(measurement_gate_inds))
for i in measurement_gate_inds:
    readout_qubits[circuit[-1].clbits[0]._index] = circuit[-1].qubits[0]._index

In [ ]:
readout_values = [ int(i, 2) for i in d[0]['job_measurements'].keys() ]
exp_readout = np.zeros(2**len(readout_qubits))
exp_readout[readout_values] = list(d[0]['job_measurements'].values())

In [ ]:
circ[0]

['rz', (51,), [1.5707963267948966]]

# Model 1

## Assumptions

There are 4 types of error:
- cross talk: One gate fires when other gates fire.
- Gate error: gates don't quite do what you expect all the time
- Relaxation error: every once in awhile a one flips to a zero (and there is a very small chance of the opposite occuring)
- Readout error

Cross talk only happens on 2 qubit gates.
If $C$ is the the operation performed by gate $g$, that gate $g'$ has an (independent) chance of firing with probability $p_{g,g'}$. where $p >> p^2$.

Qiskit-aer is mostly correct about depolarization and relaxation error.
All gate errors can model by the depolarization error.
Relaxation error is right in qiskit-aer but should be applied to every qubit and not just the ones being operated on.

Qiskit-aer is completely correct about readout error (taking the experimental results from IBM)

## Equations

$\rho^{(1)} = (1 - \sum_{g' \in G} p_{g,g'}) C_g R_T \rho^{(0)} R_T^\dagger C_g^{\dagger} + \sum_{g' \in G}  p_{g,g'} C_{g'}C_g R_T \rho^{(0)} R_T^\dagger (C_gC_{g'})^{\dagger}  $

$C_g = D_g C_{g_{ideal}}$


<!-- $\ /rho_q \leftarrow \sum E_k \rho_q E_k^\dagger$, $\rho_q$ is the density matrix of qubit $q$. -->


## Loss

readout is $[x_0, x_1 \ldots x_n]$ where $x_i \in [0,1]$ is the qubit value.


Want to determine $p

In [ ]:


class Model:
    def __init__(self, backend = None, config = None):
        if config is not None:
            self.num_qubits = config['num_qubits']
            self.num_gates = config['num_gates']
            self.connections = config['connections']
            self.error_operators = config['error_operators']
            self.readout_err = config['readout_err']
            self.cross_talk_probabilities = config['cross_talk_probabilities']
        else:
            (
                self.num_qubits,
                self.num_gates,
                self.connections,
                self.error_operators,
                self.readout_err,
            ) = process_backend(backend)
            self.cross_talk_probabilities = np.array([[1] + [0] * (len(self.connections)- 1)] * len(self.connections) ) #trainable parameters
            r = np.random.rand(len(self.cross_talk_probabilities)) / 100
            self.cross_talk_probabilities = self.cross_talk_probabilities * ( 1 - 2 * r) + r
            self.cross_talk_probabilities = torch.tensor(self.cross_talk_probabilities, requires_grad=True)
        #self.optim = torch.optim.Adagrad()

    def run_instruction(self, sys, instruction):
        gate_type, qubit_ids, params = instruction
        if gate_type == 'rz':
            ideal_operator = ideal_gates[gate_type](params[0])
        else:
            ideal_operator = ideal_gates[gate_type]
        sys.transition(self.error_operators[gate_type][qubit_ids]['relax'])
        sys.transition_qubit(self.error_operators[gate_type][qubit_ids]['depol'] * ideal_operator, qubit_ids)
        if len(qubit_ids) < 2:
            return sys
        probs = self.cross_talk_probabilities[self.connections.index(qubit_ids)]
        for cross_talk_qubits, err_operator in self.error_operators[gate_type].items():
            print(cross_talk_qubits)
            p = probs[self.connections.index(cross_talk_qubits)]
            cross_talk_operator = p * err_operator['depol'] +
            (1 - p) * np.identity(4)
            kraus(cross_talk_operator) * ideal_gates['cz']
            sys.transition(cross_talk_operator, cross_talk_qubits)
        return sys

    def run(self, circuit, readout_qubits):
        sys = System(self.num_qubits)
        for instruction in circuit:
            sys = self.run_instruction(sys, instruction)

        readout_probs = [
            sys.rho[readout_qubits,0,0] * (1 - self.readout_err[readout_qubits,0]) + sys.rho[readout_qubits,1,1] * self.readout_err[readout_qubits,1],
            sys.rho[readout_qubits,0,0] * self.readout_err[readout_qubits,0] + sys.rho[readout_qubits,1,1] * (1 - self.readout_err[readout_qubits,1])
        ]
        readout_probs = np.transpose(readout_probs)
        return readout_probs

    def train_step(self, sample):
        #self.optim.zero_grad()

        circuit, readout_qubits, exp_readout = sample
        readout_probs = self.run(circuit, readout_qubits)
        log_readout_probs = np.log(readout_probs)
        log_pred_readout = np.sum(log_readout_probs[np.arange(self.num_qubits), np.array([list(np.binary_repr(i, width=self.num_qubits)) for i in range(2**self.num_qubits)], dtype=int)],axis = 0)
        loss = - exp_readout * log_pred_readout
        #self.optim.step()
        return loss

    def config(self):
        return m.__dict__

In [ ]:
import torch


In [ ]:
m = Model(prop)

<ipython-input-30-9c5eeba70b64>:6: UserWarning: t2 > 2t1 for qubit 87. Changing 5.6838717300148796e-05 to 5.42970235219996e-05
  warnings.warn("t2 > 2t1 for qubit {}. Changing {} to {}".format(qubit, t2, 2 * t1))


In [ ]:
#circuit =  [('x', (0,), None),('x', (1,), None)  ]
m.run(circ, readout_qubits)


ValueError: Maximum allowed size exceeded

In [ ]:
sample = (circ, readout_qubits, exp_readout)
m.train_step(sample)

In [ ]:
sys = System(len(prop.qubits))
for inst in circ:
  m.run_instruction(sys, inst)

(72, 73)


RuntimeError: Can't call numpy() on Tensor that requires grad. Use tensor.detach().numpy() instead.

In [ ]:
for err in m.error_operators['cz'].values():
  err['depol'].tolist()

In [ ]:
kraus(torch.from_numpy(err['depol'][0]) * m.cross_talk_probabilities[0][0])

RuntimeError: Can't call numpy() on Tensor that requires grad. Use tensor.detach().numpy() instead.

In [ ]:
a = np.random.rand(3,9,2,2)
b = np.random.rand(9,2,2)
np.matmul(a,b).shape

(3, 9, 2, 2)

In [ ]:
import numpy as np

U = 1/np.sqrt(2) * np.array([[1,0,1,0],[0,1,0,1],[1,0,-1,0],[0,1,0,-1]])
rho = np.zeros((4,4))
rho[3,3] = 1
np.matmul(U,np.matmul(rho, U.T))

array([[ 0. ,  0. ,  0. ,  0. ],
       [ 0. ,  0.5,  0. , -0.5],
       [ 0. ,  0. ,  0. ,  0. ],
       [ 0. , -0.5,  0. ,  0.5]])

In [ ]:
import numpy as np
K = 3
E = np.arange(4*K)
E = E.reshape(K,2,2)
np.matmul(E,np.conjugate(np.swapaxes(E,1,2))).sum(0)

array([[187, 241],
       [241, 319]])

Let us look at $E_{K-1}$ and $E_{K}$ to try and get it so $\sum E_k E_k^\dagger = I$

Constraints on $E_{K-1}$:

Let $I-\sum_{k = 1}^{K-1} \sum E_k E_k^\dagger =
\begin{bmatrix}
f &g \\ \bar{g} & h \\
\end{bmatrix}$

Obviously $g$ and $\bar{g}$ are complex conjugates. Also $f$ and $h$ are real, nonnegative and $|g| \leq \sqrt{fh}|$.

In [ ]:
c = complex(2,-1)
np.arccos(c.real/ np.abs(c)), np.angle(c)

(0.46364760900080615, -0.4636476090008061)

In [ ]:
import numpy as np
from math import sqrt
def crand(**args):
    return complex(np.random.rand(**args),np.random.rand(**args))
def expi(theta):
    return np.cos(theta) + complex(0,1) * np.sin(theta)



K = 5
#slow method...
E = np.empty((K,2,2), dtype = complex)
p = 0
s = 0
q = 0
for k in range(K-1):
    p_old = p
    s_old = s
    theta = np.random.rand(4)*np.pi*2

    alpha = np.exp(-5*np.random.rand())*(1-p) #alpha is between 0 and 1-p
    p = p + alpha
    beta = np.exp(-5*np.random.rand())*(1-p) #beta is between 0 and 1-p-alpha
    p += beta

    theta_q = np.angle(q)
    abs_q = abs(q)
    u = np.sqrt( 1 - p_old - beta)
    v =  abs_q * np.sqrt(alpha) * np.cos( theta_q - theta[0] + theta[2])

    gamma_max = min( 1 - s,
                    (sqrt( 1 - p_old - abs_q * abs_q - s_old - alpha - beta + p_old * s_old + s_old * alpha + s_old * beta +  v*v / u / u  ) - v/u) / u
    )
    gamma = np.exp(-5*np.random.rand())*gamma_max

    s += gamma

    w = sqrt( 1 - p_old - alpha)
    x = sqrt( alpha * gamma * beta) * np.cos(theta[0] - theta[1] - theta[2] + theta[3]) + abs_q * np.sqrt(beta) * np.cos( theta_q - theta[1] + theta[3])



    lam_max = min( 1 - s,
                  ( sqrt( 1 - abs_q * abs_q - s_old - p_old - alpha - beta - gamma + p_old * s_old + s_old * alpha + s_old * beta + p_old * gamma + beta * gamma - 2 * np.sqrt(gamma) * v + x * x / w / w) - x / w) / w
    )

    lam = np.exp(-5*np.random.rand())*lam_max

    s += lam

    exp_i_theta = expi(theta)
    E[k] = [[np.sqrt(alpha)*exp_i_theta[0], np.sqrt(beta)*exp_i_theta[1]  ], [np.sqrt(gamma) * exp_i_theta[2],np.sqrt(lam) * exp_i_theta[3]] ]
    q += E[k,0,0] * E[k,1,0].conjugate() + E[k,0,1] * E[k,1,1].conjugate()




f,h = 1 - p, 1- s
g = 0 - q
assert f < 1
assert h < 1
assert (g* g.conjugate()).real < h*f

# phi = np.random.rand() * np.pi * 2
# gamma = np.random.rand() * np.pi * 2
# zeta = np.random.rand() * np.pi * 2

# alpha = np.random.rand()*h


ValueError: math domain error

In [ ]:
g * g.conjugate()- h * f

(0.033040143416249154+2.0221489480902563e-18j)

In [ ]:
abs_q * abs_q, q_old * q_old.conjugate()

(0.09751833915559685, (0.09751833915559684+2.9286327204288408e-18j))

In [ ]:
1 - s_old - p_old - alpha - beta - gamma - lam + p_old * s_old  + s_old * alpha + s_old * beta + p_old * gamma  + p_old * lam + alpha * lam + beta * gamma - 2 * alpha * beta * gamma * lam * np.cos(theta[0] + theta[1] - theta[2] - theta[3] )

(0.006850378792950621-3.3856837849119782e-21j)

In [ ]:
a = np.sqrt(alpha) * expi(theta[0])
b = np.sqrt(beta) * expi(theta[1])
c = np.sqrt(gamma) * expi(theta[2])
d = np.sqrt(lam) * expi(theta[3])
q_old = q - E[k,0,0] * E[k,1,0].conjugate() - E[k,0,1] * E[k,1,1].conjugate()
(a * c.conjugate() + b * d.conjugate() + q_old) * (a.conjugate() * c + b.conjugate() * d + q_old.conjugate()) - ( 1 - p_old - alpha -beta ) * (1 - s_old - gamma - lam )
out = 2 * np.sqrt(alpha * gamma * beta * lam) * np.cos(theta[0] - theta[1] - theta[2] +theta[3])
out += q_old * a.conjugate() * c + q_old * b.conjugate() * d + q_old.conjugate() * a * c.conjugate() + q_old.conjugate() * b * d.conjugate()
out += q_old * q_old.conjugate()
out -= 1 - s_old - p_old - alpha - beta - gamma - lam + p_old * s_old + s_old * alpha + s_old * beta + p_old * gamma + p_old * lam
out -= alpha * lam + beta * gamma
out

(0.0330401434162491+3.0370529376773912e-18j)

In [ ]:
1 - p_old - abs_q * abs_q - s_old - alpha - beta + p_old * s_old + s_old * alpha + s_old * beta +  v*v / u / u

-0.010917661879433983

In [ ]:
y = 1 - q * q.conjugate() - s - alpha - p - alpha

/private/var/mobile/Containers/Data/Application/B120A67F-84DC-461E-89D1-3516CBB2A156/tmp/ipykernel_1300/2998634076.py:1: RuntimeWarning: invalid value encountered in sqrt
  (np.sqrt( 1 - p_old - abs_q * abs_q - s_old - alpha - beta + p_old * s_old + s_old * alpha + s_old * beta +  v*v / u / u  ) - v/u) / u


nan

In [ ]:
1 - p_old - abs_q * abs_q - s_old - alpha - beta + p_old * s_old + s_old * alpha + s_old * beta +  v*v / (1-beta - p_old)

-0.027010538886107882

In [ ]:
(s_old - 1 - y - s_old * p_old + p_old) ** 2 - 4 * ( 1 - s_old ) * ( y * p_old - y)

-0.005675024423855701

In [ ]:
y = gamma - phi
neg_b = np.sqrt( h - alpha) * ( g.conjugate() * expi(y) + g * expi(-y) )
beta = (neg_b + np.sqrt( neg_b * neg_b + 4 * h * f * alpha - 4 * h * g * g.conjugate()))/ 2/h
beta = beta * beta
x = ((g- np.sqrt( beta * ( h - alpha) ) * expi(gamma - phi) )/ np.sqrt(alpha * (f - beta)) / expi(zeta))
theta = -np.angle( x )


a,b,c,d =  np.sqrt(beta) * expi(gamma) , np.sqrt(f-beta) * expi(zeta), np.sqrt(h - alpha) * expi(phi), np.sqrt(alpha) * expi(theta)
E_k = [[a,b],[c,d]]

print(np.matmul(E_k, np.conjugate(E_k).T).round(10))
print(np.array([[f,g],[g.conjugate(),h]]))


[[0.39239678-0.j         0.06691722+0.07991311j]
 [0.06691722-0.07991311j 0.06725962-0.j        ]]
[[0.12811347+0.j         0.08081747+0.10207228j]
 [0.08081747-0.10207228j 0.06725962+0.j        ]]


In [ ]:
E[-1] = E_k
np.matmul(E,np.conjugate(np.swapaxes(E,1,2))).sum(0)

array([[ 1.0000000e+00-6.58236808e-18j, -6.9388939e-18-1.04083409e-17j],
       [-6.9388939e-18+1.04083409e-17j,  1.0000000e+00-1.24041011e-17j]])

In [ ]:
beta * h - np.sqrt(beta) * np.sqrt( h- alpha) * ( g.conjugate() * expi(gamma - phi) + g * expi( phi - gamma) ) - f * alpha + g * g.conjugate()

(0.011329714918129508-0.19549906463141656j)

In [ ]:
print((f - beta) * alpha)
print( g * g.conjugate() - g.conjugate() * np.sqrt(beta * (h - alpha)) * expi(gamma - phi) - g * np.sqrt(beta * ( h- alpha) ) * expi(phi - gamma) + beta * (h - alpha)    )

(0.11824376349166316+6.82912980519888e-20j)
(0.11824376349166305-3.055782009131749e-20j)


In [ ]:
print(b * b.conjugate() * alpha)
print( g * g.conjugate() - g.conjugate() * a * c.conjugate() - g * a.conjugate() * c + a * a.conjugate() * c * c.conjugate() )

(0.11824376349166313+1.51782372261536e-18j)
(0.11824376349166305-6.9154990917767144e-18j)


In [ ]:
print( h - alpha + (g - a * c.conjugate()) * (g.conjugate() - a.conjugate() * c) / b / b.conjugate() )
print(h)

(0.7656306194832346+3.9239822181567035e-18j)
0.7656306194832351


In [ ]:
print(d.conjugate() * d)
print( (g - a * c.conjugate()) * (g.conjugate() - a.conjugate() * c) / b / b.conjugate())
print(alpha)

(0.5217151330826495-4.958060557684295e-20j)
(0.5217151330826497+1.907706054893799e-17j)
0.5217151330826495


In [ ]:
x = ((g- np.sqrt( beta * ( h - alpha) ) * expi(gamma - phi) )/ np.sqrt(alpha * (f - beta)) / expi(zeta))
theta = -np.angle( x )
d = np.sqrt(alpha) * expi(theta)
print(d.conjugate() * b)
print( g - a * c.conjugate() )

(0.5094549952864484+0.17090733365035407j)
(0.5094549952864484+0.17090733365035424j)


In [ ]:
(g- np.sqrt( beta * ( h - alpha) ) * expi(gamma - phi) )/ np.sqrt(f - beta) / expi(zeta), ( g- a * c.conjugate() ) / b

((-0.6937520266590521+0.20105536200038981j),
 (-0.6937520266590519+0.20105536200038973j))

In [ ]:
( g- np.sqrt(beta * (h - alpha)) * expi(gamma- phi)  ) /  np.sqrt( f - beta ) / expi(gamma)

(0.7215291235712278-0.033329520266361254j)

In [ ]:
t = np.random.rand() * 2 * np.pi
x = expi(t)
help(np.angle)

Help on _ArrayFunctionDispatcher in module numpy:

angle(z, deg=False)
    Return the angle of the complex argument.
    
    Parameters
    ----------
    z : array_like
        A complex number or sequence of complex numbers.
    deg : bool, optional
        Return angle in degrees if True, radians if False (default).
    
    Returns
    -------
    angle : ndarray or scalar
        The counterclockwise angle from the positive real axis on the complex
        plane in the range ``(-pi, pi]``, with dtype as numpy.float64.
    
        .. versionchanged:: 1.16.0
            This function works on subclasses of ndarray like `ma.array`.
    
    See Also
    --------
    arctan2
    absolute
    
    Notes
    -----
    Although the angle of the complex number 0 is undefined, ``numpy.angle(0)``
    returns the value 0.
    
    Examples
    --------
    >>> np.angle([1.0, 1.0j, 1+1j])               # in radians
    array([ 0.        ,  1.57079633,  0.78539816]) # may vary
    >>> np.ang

In [ ]:
x
np.angle(x), t

(2.8747129308232457, 2.8747129308232457)

In [ ]:
(g - a * c.conjugate())/b, expi(-theta), theta

((-0.6937520266590519+0.20105536200038973j),
 (0.998934812504538-0.04614369259740222j),
 0.04616008347614151)

In [ ]:
import sympy


In [ ]:
f,h, alpha2,beta2, alpha, beta, gamma, theta, phi, zeta = sympy.symbols("f,h, a,b,alpha beta gamma phi theta zeta", positive = True)
g = sympy.symbols('g')
i = sympy.I
f = beta2+beta

In [ ]:
a = sympy.sqrt(beta) * sympy.exp(i*gamma)
b = sympy.sqrt(f - beta) * sympy.exp(i * zeta)
c = sympy.sqrt(h - alpha) * sympy.exp(i * phi)
d = sympy.sqrt(alpha) * sympy.exp(i * theta)

M = sympy.Matrix([[a,b],[c,d]])
M

NameError: name 'sympy' is not defined

In [ ]:
soln_1 = sympy.solve(sympy.Eq(a.conjugate() * c + sympy.sqrt(f - beta) * sympy.exp(-i * zeta) * d, g.conjugate()), sympy.sqrt(beta))

In [ ]:
sympy.Eq(a.conjugate() * c + sympy.sqrt(f - beta) * sympy.exp(-i * zeta) * d, g.conjugate())

NameError: name 'sympy' is not defined

In [ ]:
M * M.adjoint().simplify

NameError: name 'M' is not defined

In [ ]:
sympy.solve(sympy.Eq(a.conjugate() * c + sympy.sqrt(f - beta) * sympy.exp(-i * zeta) * d, g.conjugate()), beta)

[]

In [ ]:
np.sqrt(alpha) * expi(phi-zeta) * np.sqrt(f-beta) + np.sqrt(beta) * np.sqrt(h-alpha) * expi(theta - gamma)-g

NameError: name 'np' is not defined

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
u,v = np.indices([11,11])
x,y = np.random.randint(100,size=2)
u = u/10 * y
v = v/10 * x
z = np.sqrt(u) *np.sqrt(x - v) + np.sqrt(y - u) * np.sqrt(v)
np.max(z), np.min(z), np.sqrt(x*y)

(47.021271782034994, 0.0, 47.02127178203499)

In [ ]:
import sympy
h,f,beta,x,y = sympy.symbols('h f beta x y', positive = True)
g = sympy.symbols('g')
eq = sympy.Eq(h*f - x, g*sympy.conjugate(g) - g * sympy.sqrt(beta * x) * sympy.exp(sympy.I * y)- sympy.conjugate(g) * sympy.sqrt(beta * x) * sympy.exp(-sympy.I * y) + beta * x)
eq

Eq(f*h - x, -sqrt(beta)*g*sqrt(x)*exp(I*y) - sqrt(beta)*sqrt(x)*exp(-I*y)*conjugate(g) + beta*x + g*conjugate(g))

In [ ]:
soln = sympy.solve(eq, sympy.sqrt(beta))

In [ ]:
soln[0]

(g*exp(2*I*y) - sqrt(4*f*h*exp(2*I*y) + g**2*exp(4*I*y) - 2*g*exp(2*I*y)*conjugate(g) - 4*x*exp(2*I*y) + conjugate(g)**2) + conjugate(g))*exp(-I*y)/(2*sqrt(x))

In [ ]:
soln[1]

(g*exp(2*I*y) + sqrt(4*f*h*exp(2*I*y) + g**2*exp(4*I*y) - 2*g*exp(2*I*y)*conjugate(g) - 4*x*exp(2*I*y) + conjugate(g)**2) + conjugate(g))*exp(-I*y)/(2*sqrt(x))

In [ ]:
print(sympy.pycode(soln[1]))

  # Not supported in Python:
  # conjugate
(1/2)*(g*math.exp(2*1j*y) + math.sqrt(4*f*h*math.exp(2*1j*y) + g**2*math.exp(4*1j*y) - 2*g*math.exp(2*1j*y)*conjugate(g) - 4*x*math.exp(2*1j*y) + conjugate(g)**2) + conjugate(g))*math.exp(-1j*y)/math.sqrt(x)


In [ ]:
h * (f-alpha) - x

4.791558000285896

In [ ]:
-np.sqrt(beta*x) * g * expi(y) - np.sqrt(beta * x) * g.conjugate() * expi(-y) + beta * x + g * g.conjugate()

(4.791558000285896+2.095968739296801e-16j)

In [ ]:
beta = np.sqrt(g * g * expi(2 * y) + g.conjugate() * g.conjugate() * expi(- 2 * y) + 2 * g * g.conjugate() - 4 * ( x- h * (f-alpha) + g * g.conjugate() ) )
beta = beta + g * expi(y) + g.conjugate() * expi(-y)
beta = beta * beta / 4/ x

In [ ]:
beta * x - np.sqrt(beta) * ( g * np.sqrt(x) * expi(y) + g.conjugate() * np.sqrt(x) * expi(-y) ) + x - h * (f-alpha) + g * g.conjugate()

(8.881784197001252e-16+1.8184129831405118e-16j)

In [ ]:
a = np.sqrt(beta) * expi(gamma)
b = np.sqrt(f - beta) * expi(zeta)
c = np.sqrt(h - alpha) * expi(phi)
d = np.sqrt(alpha) * expi( theta)

In [ ]:
f - alpha

3.245885388809227

In [ ]:
(g * g.conjugate() - a * c.conjugate() * g.conjugate() - a.conjugate() * c * g + a * a.conjugate() * c * c.conjugate() ) / ( h - c * c.conjugate() )

(5.91528939411125+8.39463376143383e-18j)

In [ ]:
h - c * c.conjugate(), alpha

NameError: name 'h' is not defined

In [ ]:
a * a.conjugate()

NameError: name 'a' is not defined

In [ ]:
import numpy as np
import sympy
CZ = np.diag([1,1,1,-1])
a,b = sympy.symbols('a b')
x = np.array([1,2])/np.sqrt(3)
x = np.kron(np.kron(x,x),x)
U1 = np.kron(CZ,np.identity(2))
U2 = np.matmul(U1, np.kron(np.identity(2), CZ))


In [ ]:
rho = np.matmul(np.array([x]).T,[x])

In [ ]:
np.matmul(U1, rho, U1)

array([[ 0.03703704,  0.07407407,  0.07407407,  0.14814815,  0.07407407,
         0.14814815,  0.14814815,  0.2962963 ],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [ 0.14814815,  0.2962963 ,  0.2962963 ,  0.59259259,  0.2962963 ,
         0.59259259,  0.59259259,  1.18518519],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [ 0.14814815,  0.2962963 ,  0.2962963 ,  0.59259259,  0.2962963 ,
         0.59259259,  0.59259259,  1.18518519],
       [-0.14814815, -0.2962963 , -0.2962963 , -0.59259259, -0.2962963 ,
        -0.59259259, -0.59259259, -1.18518519],
       [-0.2962963 , -0.59259259, -0.59259259, -1.18518519, -0.59259259,
        -1.18518519, -1.18518519, -2.37037037]])

In [ ]:
np.matmul(U2,rho,U2)

array([[ 0.03703704,  0.07407407,  0.07407407,  0.14814815,  0.07407407,
         0.14814815,  0.14814815,  0.2962963 ],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [-0.14814815, -0.2962963 , -0.2962963 , -0.59259259, -0.2962963 ,
        -0.59259259, -0.59259259, -1.18518519],
       [ 0.07407407,  0.14814815,  0.14814815,  0.2962963 ,  0.14814815,
         0.2962963 ,  0.2962963 ,  0.59259259],
       [ 0.14814815,  0.2962963 ,  0.2962963 ,  0.59259259,  0.2962963 ,
         0.59259259,  0.59259259,  1.18518519],
       [-0.14814815, -0.2962963 , -0.2962963 , -0.59259259, -0.2962963 ,
        -0.59259259, -0.59259259, -1.18518519],
       [ 0.2962963 ,  0.59259259,  0.59259259,  1.18518519,  0.59259259,
         1.18518519,  1.18518519,  2.37037037]])